In [ ]:
import matplotlib.pyplot as plt
import numpy as np
from matplotlib import cm
import matplotlib.colors
%matplotlib inline

In [ ]:
%matplotlib inline

# prepare some coordinates
side_length = 20
x, y, z = np.indices((side_length, side_length, side_length))
temp_max = 100
temp_min = 0
# draw cuboids in the top left and bottom right corners, and a link between
# them
cpu =  (x > side_length/4) & (x < 3*side_length/4) & (y > side_length/4) & (y < 3*side_length/4) & (z < side_length/10)
heatsink = ((x == 3) | (x == 5) | (x == 7) | (x == 9)| (x == 11)| (x == 13)| (x == 15)| (x == 17)) & (x > side_length/4) & (x < 3*side_length/4) & (y > side_length/4) & (y < 3*side_length/4) & (z >= side_length/10) & (z < side_length/4)
heatsink2 = ((x == 4) | (x == 6)| (x == 8)| (x == 10)| (x == 12)| (x == 14)| (x == 16)) & (x > side_length/4) & (x < 3*side_length/4) & (y > side_length/4) & (y < 3*side_length/4) & (z >= side_length/10) & (z < (side_length/10)+1)
ice =  (x > side_length/4) & (x < 3*side_length/4) & (y > side_length/4) & (y < 3*side_length/4) & (z >= side_length/10)
air_layer =  (z < side_length/10)
cube1 = (x == 1) & (y == 1)
cube2 = (x >= 5) & (y >= 5) & (z >= 5)
link = abs(x - y) + abs(y - z) + abs(z - x) <= 2
# combine the objects into a single boolean array
voxelarray = cpu | heatsink | heatsink2
#print(np.shape(cube1))
data_values = np.zeros(np.shape(voxelarray))
k_values = np.zeros(np.shape(voxelarray))
k_values += 0.5
for i in range(len(voxelarray)):
    for j in range(len(voxelarray[i])):
        for k in range(len(voxelarray[i][j])):
            if cpu[i][j][k]:
                data_values[i][j][k] = 100
                k_values[i][j][k] = 1
            elif heatsink[i][j][k] | heatsink2[i][j][k]:
                data_values[i][j][k] = 50
                k_values[i][j][k] = 1
            else:
                data_values[i][j][k] = 50
#print(k_values)
#print(np.shape(data_values))
#data_values[1,1,0] = 0
#data_values[1,1,1] = 100
#data_values[1,1,2] = 0
#print(data_values)
# set the colors of each object
"""
colors = np.empty(voxelarray.shape, dtype=object)
colors[link] = 'red'
colors[cube1] = 'blue'
colors[cube2] = 'green'
"""
norm = matplotlib.colors.Normalize(vmin=temp_min, vmax=temp_max)
colors = cm.coolwarm(norm(data_values))

#print(np.shape(data_values))
# and plot everything

fig = plt.figure()
ax = fig.add_subplot(projection='3d')
ax.voxels(voxelarray, facecolors=colors, edgecolor='none')
m = cm.ScalarMappable(cmap=plt.cm.coolwarm, norm=norm)
m.set_array([])
plt.colorbar(m)

plt.show()

In [ ]:
from matplotlib.animation import FFMpegWriter
metadata = dict(title='CPU_air_cooler2', artist='Matplotlib',comment='Wakanda is here now.')
writer = FFMpegWriter(fps=15, metadata=metadata,bitrate=200000)
fig = plt.figure(dpi=200)

In [ ]:
%matplotlib qt

"""
T_new = np.copy(data_values)
for iteration in range(100):
    #print(data_values[5,5,1])
    for i in range(0, side_length-1):
        for j in range(0, side_length-1):
            for k in range(0, side_length-1):
                T_new[i,j,k] = (data_values[i+1,j,k] + data_values[i-1,j,k] + data_values[i,j+1,k] + data_values[i,j-1,k] + data_values[i,j,k+1] + data_values[i,j,k-1])/6
    data_values = np.copy(T_new)
"""
delta_t = 10**(-2)
delta_x=delta_y=delta_z=0.2
Tnew = np.copy(data_values)
iters = 100

with writer.saving(fig, "CPU_air_cooler.mp4", dpi=200):
    nf = 100
    for iterations in range(iters):
        for i in range(1, side_length-1):
            for j in range(1, side_length-1):
                for k in range(1, side_length-1):
                    Tnew[i,j,k] = (((k_values[i,j,k]*delta_t)/((delta_x)**2))*((data_values[i+1,j,k])-(2*data_values[i,j,k])+data_values[i-1,j,k])+
                                 ((k_values[i,j,k]*delta_t)/((delta_y)**2))*((data_values[i,j+1,k])-(2*data_values[i,j,k])+data_values[i,j-1,k])+
                                 ((k_values[i,j,k]*delta_t)/((delta_z)**2))*((data_values[i,j,k+1])-(2*data_values[i,j,k])+data_values[i,j,k-1])+
                                 data_values[i,j,k])
        #if iterations%10==0:
        #    for i in range(len(voxelarray)):
        #        for j in range(len(voxelarray[i])):
        #            for k in range(len(voxelarray[i][j])):
        #                if ice[i][j][k]:
        #                    Tnew[i][j][k] = 0
        data_values = np.copy(Tnew)
        fig.clear()
        ax = fig.add_subplot(projection='3d')
        norm = matplotlib.colors.Normalize(vmin=np.min(data_values), vmax=np.max(data_values))
        colors = cm.coolwarm(norm(data_values))
        ax.voxels(voxelarray, facecolors=colors, edgecolor='none')
        plt.draw()
        plt.pause(0.01) # choose the time argument between 0.01 and 0.5
        writer.grab_frame()

In [ ]:
from matplotlib.animation import FFMpegWriter
metadata = dict(title='CPU_basic_heat_sink', artist='Matplotlib',comment='Wakanda is here now.')
writer = FFMpegWriter(fps=15, metadata=metadata,bitrate=200000)
fig = plt.figure(dpi=200)

In [ ]:
%matplotlib qt

delta_t = 10**(-2.6)
delta_x=delta_y=delta_z=0.1
Tnew = np.copy(data_values)
iters = 100

with writer.saving(fig, "CPU_basic_heat_sink.mp4", dpi=200):
    nf = 100
    for iterations in range(iters):
        for i in range(2, side_length-2):
            for j in range(2, side_length-2):
                for k in range(0, side_length-2):
                    Tnew[i,j,k] = (((k_values[i,j,k]*delta_t)/((delta_x)**2))*((data_values[i+1,j,k])-(2*data_values[i,j,k])+data_values[i-1,j,k])+
                                 ((k_values[i,j,k]*delta_t)/((delta_y)**2))*((data_values[i,j+1,k])-(2*data_values[i,j,k])+data_values[i,j-1,k])+
                                 ((k_values[i,j,k]*delta_t)/((delta_z)**2))*((data_values[i,j,k+1])-(2*data_values[i,j,k])+data_values[i,j,k-1])+
                                 data_values[i,j,k])
        data_values = np.copy(Tnew)
        fig.clear()
        ax = fig.add_subplot(projection='3d')
        norm = matplotlib.colors.Normalize(vmin=np.min(data_values), vmax=np.max(data_values))
        colors = cm.coolwarm(norm(data_values))
        ax.voxels(voxelarray, facecolors=colors, edgecolor='none')
        plt.draw()
        plt.pause(0.01) # choose the time argument between 0.01 and 0.5
        writer.grab_frame()